# Learning from Data: Workshop 2

| Date set     | Hand-in date |
|:------------------|:-----------------------------------|
|27th January 2017  | **12:00 Thursday 13th February 2017** |


This workshop is worth 10% of the total module mark.



Candidate number: ** Put your candidate number here **  

Your report should consist of your IPython notebook showing what you did, what was the
result, and what you can conclude from the exercise. Each report will be
assessed on the following criteria:

* Does it record what was done in the exercise?
* Does it permit the results to be reproduced?
* How does the work relate to the theoretical foundations discussed in lectures?
* Is it well presented?

Just write comments on the results, etc, using markdown in new cells.

### Submitting the notebooks

Only an electronic submissions is required.  Submit your notebook (the .ipynb file) to electronic copy via the  [electronic hand-in system](http://empslocal.ex.ac.uk/submit/) using the topic <cmd>2017-02-13~ECM3420~Richard Everson~Workshop 2</cmd>.

You should be able to upload the notebook directly from wherever it is on your machine.  If you're not sure where it is, type <code>pwd</code> (print working directory) in a cell to find out.

<div class="alert alert-warning">
Although you will undoubtedly work collaboratively in the workshops themselves, these are *individual* exercises.  The reports you write should be about the results *you* obtained, and your attention is drawn to the College and University guidelines on collaboration and plagiarism. 

In [ ]:
%pylab inline
figsize(8,8)

## Classification with k-nearest neighbours

In this section of the workshop you will use a k-nearest neighbours classifier to first classify some two-dimensional data that can be easily plotted.  After that we'll try it on a more complicated dataset.

First download and plot some data

In [ ]:
import wget

try: 
    X = loadtxt('raw-tremor.txt')
except IOError:
    wget.download('http://empslocal.ex.ac.uk/~reverson/ECM3420/raw-tremor.txt')
    X = loadtxt('raw-tremor.txt')
print(X.shape)

In [ ]:
t = X[:,2]
X = X[:,:2]
print(t.shape, X.shape)

Plot the data according to the labels

In [ ]:
normal = t == 1
patient = t == 0
plot(X[normal,0], X[normal,1], 'bo', label='Normal')
plot(X[patient,0], X[patient,1], 'rs', label='Patient')
legend(loc=2)

Note the disparity in the scales of the two features.

In [ ]:
# An alternative way of plotting that colours the markers according to the value of t
scatter(X[:,0], X[:,1], s=40, c=t, cmap=cm.Spectral)
colorbar(orientation='horizontal')

### Mean and standard deviation

Find the mean (centroid) and standard deviation of the features as a whole and also for each of the classes. Check that the mean and standard
  deviation make sense in terms of your scatter plot.  You could plot the location of the centroid on the scatter plot.

Make sure you understand the way the above works.  Print the values of the variables is you're not sure and use help etc to find out about plot and scatter.

### Covariance 

Use the Python command <code>cov</code> to return the covariance matrix (remember that the covariance matrix should be a 2 by 2 matrix for these data).  Check that the diagonal entries are what you expect from the standard deviations.

Write a loop to calculate the covariance matrix by hand:
\begin{align*}
   S_{ij} = \frac{1}{N-1}\sum_{n=1}^N (x_{ni} - \bar{x}_{i})(x_{nj} - \bar{x}_{j})
\end{align*}
for each $i$ and $j$.

Check that you get the same result using both methods.

Find the
correlation between the two variables $x_1$ and $x_2$ from the standardised
covariance matrix.  You can use  <code>corrcoef</code> to check your results, but you should be able to read it from the covariance matrix of the standardised data.

## k-nearest neighbour classifier

Now we will use a k-nn classifier to classify the data.  You will have to divide the data into a training and a test set.  You can use the k-nn classifier from the <code>sklearn</code> module as follows.

In [ ]:
# Divide the data into training and test sets
from numpy.random import permutation
N = X.shape[0]
I = permutation(N)   # Shuffled indices 0,..., N-1
Itr = I[:N//2]
Ite = I[N//2:]

Xtr = X[Itr,:]
ttr = t[Itr]

Xte = X[Ite,:]
tte = t[Ite]

# Make a copy of the features as you will need it later.
Xtr_copy = Xtr.copy()
Xte_copy = Xte.copy()

Plot your training and test sets to make sure that they look like a fair random division of the data.

The training data are to be used to construct the classifier. The test data, which should not be used at all during training, are used to evaluate how well the classifier works.

### Standardisation

Since the scales of the data are so different, it will be important to standardise the data before trying to classify it.


Find the mean and standard deviations of the *training* data and use these to standardise the training data.  (You can use the commands
<code>mean</code> and <code>std</code> to find the mean and standard deviation.) Use the training data mean and standard deviation to standardise the test data.  Note that it's important to use the training data statistics (rather than the test data statistics) because both data should be treated in *exactly* the same way and we might only have a single test data point to classify.

 
Plot the standardised data 
and check your result by finding its mean and covariance matrix. 


We will use the k-nearest neighbour classifier from scikit learn, which is  quite an extensive implementation of various machine learning algorithms.

In [ ]:
from sklearn import neighbors

In general you can train the clasifier using <code>Xtr</code> and <Ttr> and then make a prediction of the classes of the features in <code>Xte</code> as follows:
<pre>
knn = KNeighborsClassifier(n_neighbors=3)
knn.fit(Xtr, ttr)   # Train it

y = knn.predict(Xte)  # Predict the class of the testing data
</pre>

The next cell shows you how to classify points on a grid in feature space.  This is so that we can gain an understanding of how the classifier works for a whole range of points.  Note that this will give poor results unless you have first standardised your data.

In [ ]:
k = 5   # Chosse the number of nearest neighbours

knn = neighbors.KNeighborsClassifier(n_neighbors=k)
knn.fit(Xtr, ttr)

# Plot the prediction by the classifier of the class probability 
# (estimated from the fraction of points of each class in the k
# nearest neighbours) for data on a grid.  

N, M = 40, 30   # Make these larger to get a smoother picture

Xgrid = linspace(-3.0, 3.0, N)
Ygrid = linspace(-3.0, 3.0, M)
pred = zeros((M,N))
prob = zeros((M,N,2))
# Writing this double loop is not very efficient, but it is clear.
for ny, y in enumerate(Ygrid):
    for nx, x in enumerate(Xgrid):
        pred[ny, nx] = knn.predict([[x, y]])          # Predict expects a matrix of features
        prob[ny, nx, :] = knn.predict_proba([[x, y]]) # Probabilities of belonging to one class
pcolor(Xgrid, Ygrid, pred, cmap=cm.gray, alpha=0.2)
colorbar()
plot(Xtr[ttr==0,0], Xtr[ttr==0,1], 'b.')
plot(Xtr[ttr==1,0], Xtr[ttr==1,1], 'r.')
axis('tight')

# Plot the class probabilites
figure()
pcolor(X, Y, prob[:,:,0], cmap=cm.coolwarm, alpha=0.8)
colorbar()
plot(Xtr[ttr==0,0], Xtr[ttr==0,1], 'bo')
plot(Xtr[ttr==1,0], Xtr[ttr==1,1], 'ro')
axis('tight')


In [ ]:
from sklearn.neighbors import KNeighborsClassifier

knn = KNeighborsClassifier(n_neighbors=3)
knn.fit(Xtr, ttr)   # Train it

y = knn.predict(Xte)  # Predict the class of the testing data

Use your classifier to carry out $k=1$ classification of the
<code>Xte</code> tremor data. Following the example above,  plot the
training data according to its class and plot the test data according to
both its true class (from <code>tte</code>) and its predicted class from your
classifier.  Where the predicted class differs from the true class make
sure that you can see from the plot why the classifier has classified the
way it has. Work out the <i>classification accuracy</i> for your
classifier, that is the fraction of examples in <code>Xte</code> for which  the
classifier predicts the correct class.

Repeat the above for  $k = 3$ and $k = 10$ and give an explanation for
your results.   Automate the procedure to plot a graph of the
classification accuracy of <code>Xte</code> versus $k$ for $k$ up to about 40.  What's the best $k$ to use?  Why are smaller $k$ worse?  Why are larger $k$ worse?

Now plot the classification accuracy for the <i>training </i> data (that
is call your classifier like <code>knn.predict(Xtr)</code>).
Explain the shape of the curve.

Now use the k-nn classifier to find the accuracy using the standardised data.  How does it compare with the raw data?

### Cross validation

Above we used all the training data and guessed the value of $k$. Much better is to estimate the optimum value of $k$, but dividing the training data into a training and a validation set; the generalisation error is then estimated on the validation set and the $k$ giving the minimum error is used for making predictions about unknown data.

Better than just dividing the training data into two is to use $k$ fold cross validation (don't confuse the $k$ in $k$ cross validation with the $k$ in $k$ nearest neighbours!

To perform $k$-fold cross validation divide the training data into several (Nfold) portions/folds, use all but one of them to train the classifier, and evaluate the accuracy on the fold that you have reserved.  Do this for each fold in turn and average the error on the reserved folds to find an overall *validation error*, which is an estimate of the *generalisation error*.   Usually dividing the data into 5 or 10 folds will be enough. 


You can either write your own code to do this or use the cross validation machinery provided by scikit learn. The following cell shows how the sklearn routines may be used to produce training and validation sets automatically. More information at <http://scikit-learn.org/stable/modules/cross_validation.html>.    You will need to adapt it for your data. 

You will probably get a warning that this is deprecated, but don't worry about it!

In [ ]:
from sklearn.cross_validation import KFold

# Make our "training" data of 10 examples, each of two columns.
# These "features" have just got integers in so that you can easily see which 
# examples have been selected.
X = vstack((arange(10), arange(10))).T + 10
t = arange(10)+100   # Targets
print("Features")
print(X)
print("Targets")
print(t)
print()
print()

cv = KFold(len(t), n_folds=5)    # 5 fold CV here.

# Also try this with shuffle=True, which shuffles the data before
# splitting it.  This is useful if the data is ordered in some way that
# would lead to unbalanced training and validation sets if not shuffled. 
# It's generally a good idea to shuffle first, but can give misleading results
# if, for example, the data are ordered in time. 
# cv = KFold(len(t), n_folds=5, shuffle=True)    # 5 fold CV here.

fold = 0
for train, validation in cv:
    print('-------- Fold', fold)
    print('Train')
    print(X[train])
    print(t[train])
    print('Test')
    print(X[validation])
    print(t[validation])
    fold += 1
    # Notice that each training set consists of 8 of the 10 examples 
    # and the validation set is the remaining 2.
    # You should train the model with X[train] and t[train]
    # and estimate the generalisation error on X[validation] and 
    # t[validation].  Don't forget to average the validation error 
    # over all the folds


Make a plot of the training and validation errors as $k$ varies from 1 to, say, 50.  

*  What is the best value of $k$?  
*  What is the error on the **test** set with the best $k$?
*  Make a plot of the decision regions (as above) with the best $k$
*  What can you say about the performance of the classifier when $k$ is too large or too small?
*  How do you think the optimum $k$ will vary if the amount of training data available is larger or smaller?  Can you test your hypothesis?

### Unstandardised data

Compare the performance of the classifier on the unstandardised data.  Why are they different?  

### Sphering

Sphere  the tremor data and plot it in the sphered coordinates. Compute the mean and covariance matrix of the sphered data: are they what you expect?


Find the classification accuracy using the sphered data.

## Classifying digits

Here you'll use the k-nn classifier to distinguish between digits. You can load and plot a dataset of digit images as follows (keep executing the cell to see more digits)

In [ ]:
import sklearn.datasets
from numpy.random import randint
digits = sklearn.datasets.load_digits(n_class=10)
print(digits.data.shape)

# Pick a digit at random and plot it.  
# The title should be the number that is the digit from the target arrage
j = randint(digits.data.shape[0])
imshow(reshape(digits.data[j], (8,8)), cmap=cm.gray_r)
title("%d" % digits.target[j])

As you can see there are 1797 images arranged as 64-dimensional vectors. Choose two digits as the two classes that you'll use as the two classes and arrange them as a data and target matrix as follows.

In [ ]:
mydigits = [0, 4]  # Choose your own!
I = np.logical_or(digits.target == mydigits[0], digits.target == mydigits[1])
X = digits.data[I,:]   # Features
# Make the targets 0 or 1 coresponding to the two classes
tmp = digits.target[I]
t = zeros(X.shape[0])
for i in (0,1):
    t[tmp == mydigits[i]] = i

In [ ]:
# Check the above: the title is now the class label, 0 or 1. 
# Re-execute to check that digits are labelled consistently
j = randint(len(t))
imshow(reshape(X[j], (8,8)), cmap=cm.gray_r)
title("%d" % t[j])

### k-nn classification

Now use your k-nn classifier to classify the image vectors.  What is the accuracy?   Note that here you should (a) split your data into training and testing data and (b) use cross validation on the training data to determine the best value of $k$ before finding the accuracy on the test data.  One reasonable way of proceeding would be to split the data into equal-sized training and test sets and then use 5 or 10 fold cross validation on the training set to determine $k$.

Do the misclassified images look like the other class?